<a href="https://colab.research.google.com/github/hahmed988/Big_Data_Projects/blob/master/spark_nlp_glove.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
#Spark Configuration

!apt-get install openjdk-8-jdk-headless -qq > /dev/null
!wget -q https://www-us.apache.org/dist/spark/spark-2.4.3/spark-2.4.3-bin-hadoop2.7.tgz
!tar xf spark-2.4.3-bin-hadoop2.7.tgz

In [3]:
!ls

sample_data  spark-2.4.3-bin-hadoop2.7	spark-2.4.3-bin-hadoop2.7.tgz


In [0]:
#!rm -rf spark-2.3.3-bin-hadoop2.7.tgz.1

In [5]:
!pip install -q findspark
!pip install spark-nlp==2.0.4
!pip install -q pyspark

     |████████████████████████████████| 61kB 2.3MB/s 
     |████████████████████████████████| 215.6MB 113kB/s 
     |████████████████████████████████| 204kB 43.1MB/s 


In [0]:
import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-8-openjdk-amd64"
os.environ["SPARK_HOME"] = "/content/spark-2.4.3-bin-hadoop2.7"

In [0]:
import os
from pathlib import Path
import urllib.request
import zipfile

In [0]:
from pyspark.sql.functions import col
from pyspark.sql.functions import when
from pyspark.sql.types import DoubleType


In [0]:
from sparknlp.annotator import *
from sparknlp.common import *
from sparknlp.base import *

In [0]:
from sparknlp.embeddings import *

In [7]:
import pyspark
from pyspark.sql import SparkSession
spark = SparkSession.builder \
        .config('spark.jars', 'pysparknlp-1.0.0/lib/sparknlp.jar') \
        .config("spark.jars.packages", "JohnSnowLabs:spark-nlp:2.0.4")\
        .getOrCreate() 
spark

In [8]:
!ls

sample_data  spark-2.4.3-bin-hadoop2.7	spark-2.4.3-bin-hadoop2.7.tgz


In [9]:
from google.colab import files
files.upload()

Saving classification_dataset.csv to classification_dataset.csv


{'classification_dataset.csv': b',TARGET,TEXT\r\n0,alt.atheism,bible quiz answers article healta saturn wwc edu healta saturn wwc edu tammy healy writes cheribums ark covenant god make graven image refering idols created worshipped ark covenant wasn wrodhipped and high priest enter holy holies once year day atonement not familiar knowledgeable original language word for idol and that translator used word idol graven image had original idol you wrong suggesting determine whether interpretation you offer correct dean kaflowitz\r\n1,alt.atheism,amusing atheists and agnostics article timmbake mcl timmbake mcl ucsb edu clam bake timmons writes fallacy atheism faith hear faq beckoning once wonderful rule deleted you correct you didn conspiracy correction hard atheism faith rule don mix apples oranges can you that extermination mongols worse stalin khan conquered people unsympathetic that atrocious stalin killed millions people loved and worshipped and atheist state can worse that will not ex

In [0]:
df = spark.read.csv("classification_dataset.csv", header=True, mode="DROPMALFORMED")

In [11]:
df = df.select("TARGET", "TEXT")
df.printSchema()

root
 |-- TARGET: string (nullable = true)
 |-- TEXT: string (nullable = true)



In [0]:
df = df.na.drop()

In [0]:
# Download Glove Word Embeddings
# file = "glove.6B.zip"
# if not Path("glove.6B.zip").is_file():
#     url = "http://nlp.stanford.edu/data/glove.6B.zip"
#     print("Start downoading Glove Word Embeddings. It will take some time, please wait...")
#     urllib.request.urlretrieve(url, "glove.6B.zip")
#     print("Downloading finished")
#     print("Unzipping the files now.")
# else:
#     print("File already present.")
    
# if not Path("glove.6B.100d.txt").is_file():
#     zip_ref = zipfile.ZipFile(file, 'r')
#     zip_ref.extractall("./")
#     zip_ref.close()

In [0]:
abstract_assembler = DocumentAssembler() \
    .setInputCol("TEXT") \
    .setOutputCol("document")

In [0]:
sentence_detector = SentenceDetector() \
    .setInputCols(["document"]) \
    .setOutputCol("sentence") \
    .setUseAbbreviations(True)
    
tokenizer = Tokenizer() \
  .setInputCols(["sentence"]) \
  .setOutputCol("token")

stemmer = Stemmer() \
    .setInputCols(["token"]) \
    .setOutputCol("stem")
    
normalizer = Normalizer() \
    .setInputCols(["stem"]) \
    .setOutputCol("normalized")

nlp_pipeline = Pipeline(stages=[sentence_detector, tokenizer, stemmer, normalizer])

In [0]:
# abstract_finisher = Finisher() \
#     .setInputCols(["normalized"]) \
#     .setOutputCols(["ntokens"]) 
#     .setOutputAsArray(True) \
#     .setCleanAnnotations(True)

In [0]:
import pyspark
from pyspark.ml import Pipeline, feature, classification

stopWords = feature.StopWordsRemover.loadDefaultStopWords('english')
sw_remover = feature.StopWordsRemover(inputCol='normalized', outputCol='clean', stopWords=stopWords)

In [0]:
abstract_pipeline = Pipeline(stages=[abstract_assembler, nlp_pipeline])
#abstract_pipeline = Pipeline(stages=[abstract_assembler, nlp_pipeline])

#title_pipeline = Pipeline(stages=[title_assembler, nlp_pipeline, title_finisher])

#preproc_pipeline = Pipeline(stages=[abstract_pipeline])

In [0]:
# (trainingData, testData) = df.randomSplit([0.7, 0.3], seed = 100)
# print("Training Dataset Count: " + str(trainingData.count()))
# print("Test Dataset Count: " + str(testData.count()))

In [0]:
label_indexer = feature.StringIndexer(inputCol='TARGET', outputCol='label')
label_indexer_model = label_indexer.fit(df)
label_deindexer = feature.IndexToString(inputCol='prediction', outputCol='pred_label', 
                                         labels=label_indexer_model.labels)
trainingData, test = label_indexer_model.transform(df).randomSplit(weights=[0.8, 0.2], seed=123)

In [23]:
preproc_model = abstract_pipeline.fit(trainingData)
processed = preproc_model.transform(trainingData)
processed.show()

+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+
|     TARGET|                TEXT|label|            document|            sentence|               token|                stem|          normalized|
+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+
|alt.atheism| article horus mc...| 17.0|[[document, 0, 47...|[[document, 0, 47...|[[token, 0, 6, ar...|[[token, 0, 6, ar...|[[token, 0, 5, ar...|
|alt.atheism|age reason read r...| 17.0|[[document, 0, 74...|[[document, 0, 74...|[[token, 0, 2, ag...|[[token, 0, 2, ag...|[[token, 0, 1, ag...|
|alt.atheism|age reason read r...| 17.0|[[document, 0, 50...|[[document, 0, 50...|[[token, 0, 2, ag...|[[token, 0, 2, ag...|[[token, 0, 1, ag...|
|alt.atheism|age reason read r...| 17.0|[[document, 0, 92...|[[document, 0, 92...|[[token, 0, 2, ag...|[[token, 0, 2, ag...|

In [0]:
text2vec = feature.Word2Vec(
    vectorSize=100, minCount=5, seed=123, 
    inputCol='clean', outputCol='text_vec', 
    windowSize=5, maxSentenceLength=30
)

# text2vec = WordEmbeddings()\
#   .setInputCols(["document","token"])\
#   .setOutputCol("text_vec")\
#   .setEmbeddingsSource("glove.6B.100d.txt", 100, 2)

# text2vec = WordEmbeddings()\
#   .setInputCols(["document","token"])\
#   .setOutputCol("text_vec")\
#   .setEmbeddingsSource("glove.6B.100d.txt", 100, 2)

assembler = feature.VectorAssembler(inputCols=['text_vec'], outputCol='features')

feature_pipeline = Pipeline(stages=[text2vec, assembler])

In [0]:
# feature_model = text2vec.fit(processed)
# features = feature_model.transform(processed)
# features.show()

In [28]:
!ls

classification_dataset.csv  spark-2.4.3-bin-hadoop2.7
sample_data		    spark-2.4.3-bin-hadoop2.7.tgz


In [0]:
# word_embeddings = WordEmbeddings() \
#         .setInputCols(["TEXT", "clean"])\
#         .setOutputCol("word_embeddings")\
#         .setEmbeddingsSource('glove.6B.100d.txt', 100, 2)

In [0]:
# feature_model_we = word_embeddings.fit(processed)
# features = feature_model_we.transform(processed)
# features.show()

In [0]:
from sparknlp.pretrained import PretrainedPipeline

In [0]:
#pipeline = PretrainedPipeline("explain_document_dl", "en")

In [0]:
processed = processed.withColumnRenamed("TEXT", "text")
#newDF.show()

In [0]:
#processed.show()

In [0]:
#pretrained = pipeline.transform(processed).show()

In [0]:
word_emb = WordEmbeddingsModel.pretrained('glove_100d')


In [57]:
Processed_corpus    = word_emb.transform(processed)
Processed_corpus.show()

+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|     TARGET|                text|label|            document|            sentence|               token|                stem|          normalized|          embeddings|
+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|alt.atheism| article horus mc...| 17.0|[[document, 0, 47...|[[document, 0, 47...|[[token, 0, 6, ar...|[[token, 0, 6, ar...|[[token, 0, 5, ar...|[[word_embeddings...|
|alt.atheism|age reason read r...| 17.0|[[document, 0, 74...|[[document, 0, 74...|[[token, 0, 2, ag...|[[token, 0, 2, ag...|[[token, 0, 1, ag...|[[word_embeddings...|
|alt.atheism|age reason read r...| 17.0|[[document, 0, 50...|[[document, 0, 50...|[[token, 0, 2, ag...|[[token, 0, 2, ag...|[[token, 0, 1, ag...|[[word_embeddings...

In [58]:
Processed_corpus.show(2)

+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|     TARGET|                text|label|            document|            sentence|               token|                stem|          normalized|          embeddings|
+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|alt.atheism| article horus mc...| 17.0|[[document, 0, 47...|[[document, 0, 47...|[[token, 0, 6, ar...|[[token, 0, 6, ar...|[[token, 0, 5, ar...|[[word_embeddings...|
|alt.atheism|age reason read r...| 17.0|[[document, 0, 74...|[[document, 0, 74...|[[token, 0, 2, ag...|[[token, 0, 2, ag...|[[token, 0, 1, ag...|[[word_embeddings...|
+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------

In [0]:
# label_indexer = feature.StringIndexer(inputCol='TARGET', outputCol='label')
# label_indexer_model = label_indexer.fit(label_indexer_model = label_indexer.fit(df))
# label_deindexer = feature.IndexToString(inputCol='prediction', outputCol='pred_label', 
#                                          labels=label_indexer_model.labels)
# train, test = label_indexer_model.transform(non_empty_texts).randomSplit(weights=[0.8, 0.2], seed=123)

In [0]:

finisher = Finisher() \
    .setInputCols(["embeddings"]) \
    .setIncludeMetadata(True)\
    .setOutputAsArray(True)

In [61]:
# feature_model = finisher.fit(Processed_corpus)
# features = feature_model.transform(Processed_corpus)
# features.show()
Processed_corpus.show()

+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|     TARGET|                text|label|            document|            sentence|               token|                stem|          normalized|          embeddings|
+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|alt.atheism| article horus mc...| 17.0|[[document, 0, 47...|[[document, 0, 47...|[[token, 0, 6, ar...|[[token, 0, 6, ar...|[[token, 0, 5, ar...|[[word_embeddings...|
|alt.atheism|age reason read r...| 17.0|[[document, 0, 74...|[[document, 0, 74...|[[token, 0, 2, ag...|[[token, 0, 2, ag...|[[token, 0, 1, ag...|[[word_embeddings...|
|alt.atheism|age reason read r...| 17.0|[[document, 0, 50...|[[document, 0, 50...|[[token, 0, 2, ag...|[[token, 0, 2, ag...|[[token, 0, 1, ag...|[[word_embeddings...

In [62]:
Processed_corpus.select("TARGET", "text", Processed_corpus.embeddings['sentence_embeddings'], Processed_corpus.embeddings['embeddings'], Processed_corpus.embeddings['result']).show()

+-----------+--------------------+------------------------------+---------------------+--------------------+
|     TARGET|                text|embeddings.sentence_embeddings|embeddings.embeddings|   embeddings.result|
+-----------+--------------------+------------------------------+---------------------+--------------------+
|alt.atheism| article horus mc...|          [[], [], [], [], ...| [[-0.55661, -0.11...|[article, horus, ...|
|alt.atheism|age reason read r...|          [[], [], [], [], ...| [[0.55197, 1.0472...|[age, reason, rea...|
|alt.atheism|age reason read r...|          [[], [], [], [], ...| [[0.55197, 1.0472...|[age, reason, rea...|
|alt.atheism|age reason read r...|          [[], [], [], [], ...| [[0.55197, 1.0472...|[age, reason, rea...|
|alt.atheism|albert sabin wpr ...|          [[], [], [], [], ...| [[0.43446, -0.181...|[albert, sabin, w...|
|alt.atheism|alleged deathbed ...|          [[], [], [], [], ...| [[1.0285, -0.3577...|[alleged, deathbe...|
|alt.atheism|alt at

In [63]:
Processed_corpus = Processed_corpus.withColumn("raw_embedding", Processed_corpus.embeddings['embeddings'])
Processed_corpus.show()

+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|     TARGET|                text|label|            document|            sentence|               token|                stem|          normalized|          embeddings|       raw_embedding|
+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|alt.atheism| article horus mc...| 17.0|[[document, 0, 47...|[[document, 0, 47...|[[token, 0, 6, ar...|[[token, 0, 6, ar...|[[token, 0, 5, ar...|[[word_embeddings...|[[-0.55661, -0.11...|
|alt.atheism|age reason read r...| 17.0|[[document, 0, 74...|[[document, 0, 74...|[[token, 0, 2, ag...|[[token, 0, 2, ag...|[[token, 0, 1, ag...|[[word_embeddings...|[[0.55197, 1.0472...|
|alt.atheism|age reason read r...| 17.0|[[document, 0, 50...

In [64]:
Processed_corpus = Processed_corpus.withColumn("sentence_embedding", Processed_corpus.embeddings['sentence_embeddings'])
Processed_corpus.show()

+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|     TARGET|                text|label|            document|            sentence|               token|                stem|          normalized|          embeddings|       raw_embedding|  sentence_embedding|
+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|alt.atheism| article horus mc...| 17.0|[[document, 0, 47...|[[document, 0, 47...|[[token, 0, 6, ar...|[[token, 0, 6, ar...|[[token, 0, 5, ar...|[[word_embeddings...|[[-0.55661, -0.11...|[[], [], [], [], ...|
|alt.atheism|age reason read r...| 17.0|[[document, 0, 74...|[[document, 0, 74...|[[token, 0, 2, ag...|[[token, 0, 2, ag...|[[token, 0, 1, ag...|[[word_embeddings..

In [65]:
Processed_corpus.printSchema()

root
 |-- TARGET: string (nullable = true)
 |-- text: string (nullable = true)
 |-- label: double (nullable = false)
 |-- document: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- annotatorType: string (nullable = true)
 |    |    |-- begin: integer (nullable = false)
 |    |    |-- end: integer (nullable = false)
 |    |    |-- result: string (nullable = true)
 |    |    |-- metadata: map (nullable = true)
 |    |    |    |-- key: string
 |    |    |    |-- value: string (valueContainsNull = true)
 |    |    |-- embeddings: array (nullable = true)
 |    |    |    |-- element: float (containsNull = false)
 |    |    |-- sentence_embeddings: array (nullable = true)
 |    |    |    |-- element: float (containsNull = false)
 |-- sentence: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- annotatorType: string (nullable = true)
 |    |    |-- begin: integer (nullable = false)
 |    |    |-- end: integer (nullable =

In [0]:
import numpy as np

def mean_embedding(X):
        return np.array([np.mean(vectors) for vectors in X])

In [67]:
Test = [[50,11,5], [10,11,2],[1,2]]
result = mean_embedding(Test)
result.tolist()

[22.0, 7.666666666666667, 1.5]

In [0]:
from pyspark.sql.types import IntegerType, FloatType, ArrayType, DoubleType
from pyspark.sql.functions import udf
#mean_embedding_udf_int = udf(lambda z: mean_embedding(z).tolist(), FloatType())
mean_embedding_udf_int = udf(lambda z: mean_embedding(z).tolist(), ArrayType(FloatType(), containsNull=False))
#list(set(x))

In [69]:
#Processed_corpus = Processed_corpus.select('raw_embedding', mean_embedding_udf_int('raw_embedding').alias('raw_embedding_sent')).show()
Processed_corpus = Processed_corpus.withColumn('raw_embedding_sent', mean_embedding_udf_int('raw_embedding'))
Processed_corpus.show()

+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|     TARGET|                text|label|            document|            sentence|               token|                stem|          normalized|          embeddings|       raw_embedding|  sentence_embedding|  raw_embedding_sent|
+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|alt.atheism| article horus mc...| 17.0|[[document, 0, 47...|[[document, 0, 47...|[[token, 0, 6, ar...|[[token, 0, 6, ar...|[[token, 0, 5, ar...|[[word_embeddings...|[[-0.55661, -0.11...|[[], [], [], [], ...|[-0.007834503, 0....|
|alt.atheism|age reason read r...| 17.0|[[document, 0, 74...|[[document, 0, 74..

In [70]:
Processed_corpus.printSchema()

root
 |-- TARGET: string (nullable = true)
 |-- text: string (nullable = true)
 |-- label: double (nullable = false)
 |-- document: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- annotatorType: string (nullable = true)
 |    |    |-- begin: integer (nullable = false)
 |    |    |-- end: integer (nullable = false)
 |    |    |-- result: string (nullable = true)
 |    |    |-- metadata: map (nullable = true)
 |    |    |    |-- key: string
 |    |    |    |-- value: string (valueContainsNull = true)
 |    |    |-- embeddings: array (nullable = true)
 |    |    |    |-- element: float (containsNull = false)
 |    |    |-- sentence_embeddings: array (nullable = true)
 |    |    |    |-- element: float (containsNull = false)
 |-- sentence: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- annotatorType: string (nullable = true)
 |    |    |-- begin: integer (nullable = false)
 |    |    |-- end: integer (nullable =

In [0]:
#import pyspark.sql.functions as F

pad_fix_length = udf(lambda arr: arr[:50] + [0] * (50 - len(arr[:50])), ArrayType(FloatType()))

Processed_corpus = Processed_corpus.withColumn('feature_indices', pad_fix_length("raw_embedding_sent"))

In [74]:
from pyspark.ml.linalg import Vectors, VectorUDT
#from pyspark.sql.functions import udf
list_to_vector_udf = udf(lambda l: Vectors.dense(l), VectorUDT())
Processed_vector = Processed_corpus.withColumn("raw_embedding_sent_vector", list_to_vector_udf("feature_indices"))
Processed_vector.show()

+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-------------------------+
|     TARGET|                text|label|            document|            sentence|               token|                stem|          normalized|          embeddings|       raw_embedding|  sentence_embedding|  raw_embedding_sent|     feature_indices|raw_embedding_sent_vector|
+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-------------------------+
|alt.atheism| article horus mc...| 17.0|[[document, 0, 47...|[[document, 0, 47...|[[token, 0, 6, ar...|[[token, 0, 6, ar...|[[token, 0, 5, ar...|[[word_embeddings...|[[-

In [75]:
Processed_vector.printSchema()

root
 |-- TARGET: string (nullable = true)
 |-- text: string (nullable = true)
 |-- label: double (nullable = false)
 |-- document: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- annotatorType: string (nullable = true)
 |    |    |-- begin: integer (nullable = false)
 |    |    |-- end: integer (nullable = false)
 |    |    |-- result: string (nullable = true)
 |    |    |-- metadata: map (nullable = true)
 |    |    |    |-- key: string
 |    |    |    |-- value: string (valueContainsNull = true)
 |    |    |-- embeddings: array (nullable = true)
 |    |    |    |-- element: float (containsNull = false)
 |    |    |-- sentence_embeddings: array (nullable = true)
 |    |    |    |-- element: float (containsNull = false)
 |-- sentence: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- annotatorType: string (nullable = true)
 |    |    |-- begin: integer (nullable = false)
 |    |    |-- end: integer (nullable =

In [76]:
from pyspark.ml.feature import VectorAssembler
from pyspark.sql.types import array

assembler = VectorAssembler(
    inputCols=['raw_embedding_sent_vector'],
    outputCol="features")
output = assembler.transform(Processed_vector)
output.show()

+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-------------------------+--------------------+
|     TARGET|                text|label|            document|            sentence|               token|                stem|          normalized|          embeddings|       raw_embedding|  sentence_embedding|  raw_embedding_sent|     feature_indices|raw_embedding_sent_vector|            features|
+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-------------------------+--------------------+
|alt.atheism| article horus mc...| 17.0|[[document, 0, 47...|[[document, 0, 47...|[[token, 0, 6, ar...|[[t

In [0]:
from pyspark.ml.classification import MultilayerPerceptronClassifier
mlpc = MultilayerPerceptronClassifier(maxIter=100, seed=123, layers=[50, 75, 20])
model_pipeline = Pipeline(stages=[mlpc, label_deindexer])
model = model_pipeline.fit(output)

In [78]:
predictions = model.transform(output)
predictions.show()

+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-------------------------+--------------------+--------------------+--------------------+----------+--------------------+
|     TARGET|                text|label|            document|            sentence|               token|                stem|          normalized|          embeddings|       raw_embedding|  sentence_embedding|  raw_embedding_sent|     feature_indices|raw_embedding_sent_vector|            features|       rawPrediction|         probability|prediction|          pred_label|
+-----------+--------------------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+------

In [0]:
from pyspark.ml.classification import LogisticRegression
lr = LogisticRegression(maxIter=20, family = "multinomial")
model_pipeline = Pipeline(stages=[lr, label_deindexer])

# Train model with Training Data
#lrModel = lr.fit(trainingData)
lrModel = model_pipeline.fit(output)

In [0]:
model = model_pipeline.fit(Processed_vector)

In [0]:
Processed_corpus.select(Processed_corpus.sentence_embedding.getItem(0), Processed_corpus.sentence_embedding.getItem(2)).show()

In [0]:
Processed_corpus.select(Processed_corpus.raw_embedding.getItem(0), Processed_corpus.raw_embedding.getItem(100)).show()

In [0]:
from pyspark.ml.classification import LogisticRegression
lr = LogisticRegression(maxIter=50, regParam=0.3, elasticNetParam=0, featuresCol='raw_embedding').setFamily("multinomial")
lrModel = lr.fit(Processed_corpus).transform(Processed_corpus)